# Customer segmentation analysis

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import torch
import ydata_profiling
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import plotly.subplots as sp
import plotly.figure_factory as ff


In [2]:
device = 'mps' if torch.backends.mps.is_available() else 'cpu'

In [3]:
data = pd.read_csv('/Users/paula/Documents/Portfolio/NoAConnect/NoA-Connect-JrDataScience-Case(in).csv', encoding='utf')

In [5]:
# Generate a profile report for the data
profile = ydata_profiling.ProfileReport(data, title="NoA Connect Data Profiling Report", explorative=True)

# Display the report in the notebook
profile.to_notebook_iframe()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Convert purchases to euro

In [6]:
# Define conversion rates
usd_to_eur = 0.92
gbp_to_eur = 1.19

# Create a copy of the dataframe to avoid modifying the original
data_converted = data.copy()

# Create a new column for the converted amounts
data_converted['purchase_amount_eur'] = 0.0

# Convert USD to EUR
mask_usd = data_converted['currency'] == 'USD'
data_converted.loc[mask_usd, 'purchase_amount_eur'] = data_converted.loc[mask_usd, 'purchase_amount'] * usd_to_eur

# Convert GBP to EUR
mask_gbp = data_converted['currency'] == 'GBP'
data_converted.loc[mask_gbp, 'purchase_amount_eur'] = data_converted.loc[mask_gbp, 'purchase_amount'] * gbp_to_eur

# For rows that are already in EUR, just copy the original amount
mask_eur = data_converted['currency'] == 'EUR'
data_converted.loc[mask_eur, 'purchase_amount_eur'] = data_converted.loc[mask_eur, 'purchase_amount']

# Display the first few rows to verify the conversion
print("Sample of data with converted purchase amounts:")
print(data_converted[['purchase_amount', 'currency', 'purchase_amount_eur']].head())

# Summary statistics of the converted amounts
print("\nSummary statistics of purchase amounts in EUR:")
print(data_converted['purchase_amount_eur'].describe())


Sample of data with converted purchase amounts:
   purchase_amount currency  purchase_amount_eur
0            15.29      EUR              15.2900
1            37.19      EUR              37.1900
2            56.37      EUR              56.3700
3            24.19      EUR              24.1900
4            24.79      USD              22.8068

Summary statistics of purchase amounts in EUR:
count    51948.000000
mean        56.459821
std        207.650503
min          0.000000
25%         17.020600
50%         25.190000
75%         41.980000
max      13976.400000
Name: purchase_amount_eur, dtype: float64


## Feature engineering

In [7]:
# Feature Engineering

# Convert date_of_purchase to datetime if it's not already
data_converted['order_date'] = pd.to_datetime(data_converted['order_date'])

# Get the most recent date in the dataset to calculate recency
most_recent_date = data_converted['order_date'].max()
print(f"Most recent purchase date in the dataset: {most_recent_date}")

# Group by customer_id to calculate features
customer_features = data_converted.groupby('customer_id').agg(
    # Recency: Days since last purchase
    recency=('order_date', lambda x: (most_recent_date - x.max()).days),
    
    # Frequency: Number of transactions per customer
    frequency=('order_id', 'count'),
    
    # Monetary: Average purchase amount in EUR
    monetary=('purchase_amount_eur', 'mean'),  # Changed 'average' to 'mean'
    
    # Purchase variability: Standard deviation of purchase amounts
    purchase_variability=('purchase_amount_eur', 'std'),
    
    # First purchase date
    first_purchase=('order_date', 'min'),
    
    # Last purchase date
    last_purchase=('order_date', 'max')
).reset_index()

# Handle NaN values in purchase_variability (customers with only one purchase)
customer_features['purchase_variability'].fillna(0, inplace=True)

# Calculate customer tenure in days
customer_features['tenure_days'] = (customer_features['last_purchase'] - customer_features['first_purchase']).dt.days
customer_features['tenure_days'].fillna(0, inplace=True)  # For customers with only one purchase

# Additional Feature 1: Average purchases per day (purchase frequency)
# For customers with tenure > 0, calculate purchases per day
customer_features['purchases_per_day'] = 0.0  # Initialize with 0
mask = customer_features['tenure_days'] > 0
customer_features.loc[mask, 'purchases_per_day'] = customer_features.loc[mask, 'frequency'] / customer_features.loc[mask, 'tenure_days']

# Additional Feature 2: Average spend per day
customer_features['spend_per_day'] = 0.0  # Initialize with 0
customer_features.loc[mask, 'spend_per_day'] = (customer_features.loc[mask, 'monetary'] * customer_features.loc[mask, 'frequency']) / customer_features.loc[mask, 'tenure_days']

# Additional Feature 3: Recency ratio (recency relative to tenure)
# This shows how recently a customer has purchased relative to their entire history
customer_features['recency_ratio'] = 1.0  # Initialize with 1 (worst case: most recent purchase was at the beginning)
customer_features.loc[mask, 'recency_ratio'] = customer_features.loc[mask, 'recency'] / customer_features.loc[mask, 'tenure_days']

# Additional Feature 4: Customer value score (combining monetary and frequency)
# Normalize monetary and frequency to 0-1 scale
monetary_max = customer_features['monetary'].max()
frequency_max = customer_features['frequency'].max()
customer_features['customer_value_score'] = (0.5 * (customer_features['monetary'] / monetary_max) + 
                                            0.5 * (customer_features['frequency'] / frequency_max))

# Display the first few rows of the customer features
print("\nSample of customer features:")
print(customer_features.head())

# Summary statistics of the features
print("\nSummary statistics of customer features:")
print(customer_features.describe())

# Visualize the distribution of key metrics using plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create subplots
fig = make_subplots(rows=2, cols=2, 
                    subplot_titles=('Recency Distribution', 
                                   'Frequency Distribution', 
                                   'Monetary Distribution', 
                                   'Purchase Variability Distribution'))

# Add histograms to each subplot
fig.add_trace(
    go.Histogram(x=customer_features['recency'], 
                 marker_color='skyblue',
                 opacity=0.75,
                 name='Recency'),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=customer_features['frequency'], 
                 marker_color='lightgreen',
                 opacity=0.75,
                 name='Frequency'),
    row=1, col=2
)

fig.add_trace(
    go.Histogram(x=customer_features['monetary'], 
                 marker_color='salmon',
                 opacity=0.75,
                 name='Monetary'),
    row=2, col=1
)

fig.add_trace(
    go.Histogram(x=customer_features['purchase_variability'], 
                 marker_color='purple',
                 opacity=0.75,
                 name='Purchase Variability'),
    row=2, col=2
)

# Update layout
fig.update_layout(
    height=800,
    width=1000,
    title_text="Customer Feature Distributions",
    showlegend=False
)

# Update x and y axis labels
fig.update_xaxes(title_text="Days Since Last Purchase", row=1, col=1)
fig.update_xaxes(title_text="Number of Transactions", row=1, col=2)
fig.update_xaxes(title_text="Average Purchase Amount (EUR)", row=2, col=1)
fig.update_xaxes(title_text="Standard Deviation of Purchase Amounts", row=2, col=2)

fig.update_yaxes(title_text="Number of Customers", row=1, col=1)
fig.update_yaxes(title_text="Number of Customers", row=1, col=2)
fig.update_yaxes(title_text="Number of Customers", row=2, col=1)
fig.update_yaxes(title_text="Number of Customers", row=2, col=2)

# Display the figure
fig.show()

# Create a second figure to visualize the new features
fig2 = make_subplots(rows=2, cols=2, 
                    subplot_titles=('Purchases Per Day Distribution', 
                                   'Spend Per Day Distribution', 
                                   'Recency Ratio Distribution', 
                                   'Customer Value Score Distribution'))

# Add histograms for the new features
fig2.add_trace(
    go.Histogram(x=customer_features['purchases_per_day'], 
                 marker_color='teal',
                 opacity=0.75,
                 name='Purchases Per Day'),
    row=1, col=1
)

fig2.add_trace(
    go.Histogram(x=customer_features['spend_per_day'], 
                 marker_color='orange',
                 opacity=0.75,
                 name='Spend Per Day'),
    row=1, col=2
)

fig2.add_trace(
    go.Histogram(x=customer_features['recency_ratio'], 
                 marker_color='magenta',
                 opacity=0.75,
                 name='Recency Ratio'),
    row=2, col=1
)

fig2.add_trace(
    go.Histogram(x=customer_features['customer_value_score'], 
                 marker_color='gold',
                 opacity=0.75,
                 name='Customer Value Score'),
    row=2, col=2
)

# Update layout
fig2.update_layout(
    height=800,
    width=1000,
    title_text="Additional Customer Feature Distributions",
    showlegend=False
)

# Update x and y axis labels
fig2.update_xaxes(title_text="Purchases Per Day", row=1, col=1)
fig2.update_xaxes(title_text="Spend Per Day (EUR)", row=1, col=2)
fig2.update_xaxes(title_text="Recency Ratio", row=2, col=1)
fig2.update_xaxes(title_text="Customer Value Score", row=2, col=2)

fig2.update_yaxes(title_text="Number of Customers", row=1, col=1)
fig2.update_yaxes(title_text="Number of Customers", row=1, col=2)
fig2.update_yaxes(title_text="Number of Customers", row=2, col=1)
fig2.update_yaxes(title_text="Number of Customers", row=2, col=2)

# Display the second figure
fig2.show()


Most recent purchase date in the dataset: 2025-01-22 00:00:00

Sample of customer features:
                            customer_id  recency  frequency    monetary  \
0  00235c62-e617-4eb0-a050-470c9f30e87f      441          1   26.990000   
1  00341635-2bff-4605-b3d0-ea405649659d        7          3   90.016667   
2  003fb56f-aa7f-4dd9-83bd-2209bb1076d4      224          1  129.520000   
3  004c365f-ed0a-4287-af51-77c29fc32803      128          2   30.275000   
4  004db925-5b13-4cf3-baac-df11e6e9b04b      203          2   59.600000   

   purchase_variability first_purchase last_purchase  tenure_days  \
0              0.000000     2023-11-08    2023-11-08            0   
1              8.440292     2024-03-20    2025-01-15          301   
2              0.000000     2024-06-12    2024-06-12            0   
3             12.296587     2024-07-30    2024-09-16           48   
4             37.349380     2024-06-17    2024-07-03           16   

   purchases_per_day  spend_per_day  recen

/var/folders/wf/w51yjp2n2y96hhzrphbqww_00000gn/T/ipykernel_32874/2338307557.py:32: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  customer_features['purchase_variability'].fillna(0, inplace=True)
/var/folders/wf/w51yjp2n2y96hhzrphbqww_00000gn/T/ipykernel_32874/2338307557.py:36: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are 

In [8]:
customer_features.describe()

recency    frequency     monetary  purchase_variability  \
count  7373.000000  7373.000000  7373.000000           7373.000000   
mean    228.908857     7.045707    83.330540             34.539105   
min       0.000000     1.000000     0.000000              0.000000   
25%     100.000000     1.000000    20.000800              0.000000   
50%     224.000000     1.000000    36.170000              0.000000   
75%     334.000000     2.000000    76.280000             17.559689   
max     735.000000  3771.000000  4422.580000           3354.627947   
std     149.781306    73.927900   192.341788            130.938596   

                      first_purchase                  last_purchase  \
count                           7373                           7373   
mean   2024-04-16 01:16:45.343822080  2024-06-07 02:11:14.786382848   
min              2023-01-01 00:00:00            2023-01-18 00:00:00   
25%              2023-12-26 00:00:00            2024-02-23 00:00:00   
50%              2024-04-15 00:00:00            2024-06-12 00:00:00   
75%              2024-08-13 00:00:00            2024-10-14 00:00:00   
max              2025-01-22 00:00:00            2025-01-22 00:00:00   
std                              NaN                            NaN   

       tenure_days  purchases_per_day  spend_per_day  recency_ratio  \
count  7373.000000        7373.000000    7373.000000    7373.000000   
mean     52.037841           0.066325       4.831678       5.038983   
min       0.000000           0.000000       0.000000       0.000000   
25%       0.000000           0.000000       0.000000       1.000000   
50%       0.000000           0.000000       0.000000       1.000000   
75%      45.000000           0.028090       1.669267       1.000000   
max     750.000000          21.410256    2188.930000     600.000000   
std     106.599728           0.408738      37.291171      27.146557   

       customer_value_score  
count           7373.000000  
mean               0.010355  
min                0.000133  
25%                0.002506  
50%                0.004526  
75%                0.009644  
max                0.502445  
std                0.023733

In [9]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Select features for clustering
# Core RFM features plus additional engineered features
features_for_clustering = [
    'recency', 
    'frequency', 
    'monetary', 
    'purchase_variability',
    'tenure_days'
    # Uncomment these if you want to include additional features
    # 'purchases_per_day',
    # 'spend_per_day',
    # 'recency_ratio',
    # 'customer_value_score'
]

# Create feature matrix X from selected features
X_raw = customer_features[features_for_clustering].copy()

# Check for and handle missing values
print(f"Missing values in features:\n{X_raw.isna().sum()}")
X_raw.fillna(X_raw.mean(), inplace=True)

# Standardize the features
scaler = StandardScaler()
X = scaler.fit_transform(X_raw)

print(f"Shape of standardized feature matrix: {X.shape}")

# Perform PCA
n_components = min(len(features_for_clustering), 5)  # Keep up to 5 components
pca = PCA(n_components=n_components)
X_pca = pca.fit_transform(X)

# Print explained variance ratio
explained_variance = pca.explained_variance_ratio_
cumulative_variance = np.cumsum(explained_variance)

print("\nPCA Results:")
for i, (var, cum_var) in enumerate(zip(explained_variance, cumulative_variance)):
    print(f"PC{i+1}: {var:.4f} of variance ({cum_var:.4f} cumulative)")

# Create a DataFrame with PCA results for easier plotting
pca_df = pd.DataFrame(
    data=X_pca, 
    columns=[f'PC{i+1}' for i in range(X_pca.shape[1])]
)

# Create a visualization of the explained variance
fig_variance = go.Figure()
fig_variance.add_trace(
    go.Bar(
        x=[f'PC{i+1}' for i in range(n_components)],
        y=explained_variance,
        name='Individual Explained Variance'
    )
)
fig_variance.add_trace(
    go.Scatter(
        x=[f'PC{i+1}' for i in range(n_components)],
        y=cumulative_variance,
        name='Cumulative Explained Variance',
        mode='lines+markers'
    )
)
fig_variance.update_layout(
    title="PCA Explained Variance",
    xaxis_title="Principal Components",
    yaxis_title="Explained Variance Ratio",
    yaxis=dict(range=[0, 1]),
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1)
)
fig_variance.show()

# Create scatter plot for first two principal components
fig_pca = px.scatter(
    pca_df, x='PC1', y='PC2',
    title='PCA: First Two Principal Components',
    opacity=0.7
)
fig_pca.update_layout(
    width=800, height=600,
    xaxis_title=f"PC1 ({explained_variance[0]:.2%} variance)",
    yaxis_title=f"PC2 ({explained_variance[1]:.2%} variance)"
)
fig_pca.show()

# Create a biplot to visualize feature contributions to principal components
# Calculate feature loadings
loadings = pca.components_.T * np.sqrt(pca.explained_variance_)

# Create biplot
fig_biplot = go.Figure()

# Add scatter plot of PC scores
fig_biplot.add_trace(
    go.Scatter(
        x=X_pca[:, 0],
        y=X_pca[:, 1],
        mode='markers',
        marker=dict(size=6, opacity=0.6),
        name='Customers'
    )
)

# Add feature vectors
for i, feature in enumerate(features_for_clustering):
    fig_biplot.add_annotation(
        x=loadings[i, 0] * 3,  # Scale for visibility
        y=loadings[i, 1] * 3,  # Scale for visibility
        ax=0, ay=0,
        xanchor="center",
        yanchor="bottom",
        text=feature,
        showarrow=True,
        arrowhead=1,
        arrowsize=1,
        arrowwidth=2
    )

# Update layout
fig_biplot.update_layout(
    title="PCA Biplot: Features and Principal Components",
    xaxis_title=f"PC1 ({explained_variance[0]:.2%} variance)",
    yaxis_title=f"PC2 ({explained_variance[1]:.2%} variance)",
    width=900,
    height=700,
    xaxis=dict(
        range=[-4, 4]
    ),
    yaxis=dict(
        range=[-4, 4]
    )
)
fig_biplot.show()

# Add PCA components to the customer_features DataFrame for further analysis
pca_columns = [f'PC{i+1}' for i in range(X_pca.shape[1])]
customer_features_pca = customer_features.copy()
for i, col in enumerate(pca_columns):
    customer_features_pca[col] = X_pca[:, i]

print("\nCustomer features with PCA components:")
print(customer_features_pca.head())

# Save the standardized features and PCA results for clustering
X_for_clustering = X  # Use standardized features for clustering

# Alternatively, use PCA results for clustering if you want dimension reduction
# Determine how many components to keep based on explained variance (e.g., 90%)
n_components_90pct = np.argmax(cumulative_variance >= 0.9) + 1
print(f"\nNumber of components needed to explain 90% of variance: {n_components_90pct}")

X_pca_for_clustering = X_pca[:, :n_components_90pct]
print(f"Shape of PCA-reduced feature matrix for clustering: {X_pca_for_clustering.shape}")

Missing values in features:
recency                 0
frequency               0
monetary                0
purchase_variability    0
tenure_days             0
dtype: int64
Shape of standardized feature matrix: (7373, 5)

PCA Results:
PC1: 0.3543 of variance (0.3543 cumulative)
PC2: 0.2584 of variance (0.6127 cumulative)
PC3: 0.1820 of variance (0.7947 cumulative)
PC4: 0.1248 of variance (0.9195 cumulative)
PC5: 0.0805 of variance (1.0000 cumulative)



Customer features with PCA components:
                            customer_id  recency  frequency    monetary  \
0  00235c62-e617-4eb0-a050-470c9f30e87f      441          1   26.990000   
1  00341635-2bff-4605-b3d0-ea405649659d        7          3   90.016667   
2  003fb56f-aa7f-4dd9-83bd-2209bb1076d4      224          1  129.520000   
3  004c365f-ed0a-4287-af51-77c29fc32803      128          2   30.275000   
4  004db925-5b13-4cf3-baac-df11e6e9b04b      203          2   59.600000   

   purchase_variability first_purchase last_purchase  tenure_days  \
0              0.000000     2023-11-08    2023-11-08            0   
1              8.440292     2024-03-20    2025-01-15          301   
2              0.000000     2024-06-12    2024-06-12            0   
3             12.296587     2024-07-30    2024-09-16           48   
4             37.349380     2024-06-17    2024-07-03           16   

   purchases_per_day  spend_per_day  recency_ratio  customer_value_score  \
0           0.0000

In [10]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score, davies_bouldin_score
from sklearn.utils import resample
from scipy.spatial.distance import cdist
from sklearn.preprocessing import StandardScaler

# If you're using PCA-reduced data, uncomment this line
# X = X_pca_for_clustering

# 1. DETERMINE OPTIMAL NUMBER OF CLUSTERS

# Range of k values to try
k_range = range(2, 11)

# Initialize lists to store metrics
inertia_values = []
silhouette_scores = []
davies_bouldin_scores = []

# Calculate metrics for each k
for k in k_range:
    # Fit K-means
    kmeans = KMeans(n_clusters=k, random_state=42, n_init=10)
    kmeans.fit(X)
    
    # Calculate inertia (within-cluster sum of squares)
    inertia_values.append(kmeans.inertia_)
    
    # Calculate silhouette score
    labels = kmeans.labels_
    silhouette_avg = silhouette_score(X, labels)
    silhouette_scores.append(silhouette_avg)
    
    # Calculate Davies-Bouldin index
    db_score = davies_bouldin_score(X, labels)
    davies_bouldin_scores.append(db_score)
    
    print(f"k={k}, Inertia={kmeans.inertia_:.2f}, Silhouette Score={silhouette_avg:.4f}, Davies-Bouldin={db_score:.4f}")

# Create a figure with 3 subplots for the metrics
fig = make_subplots(rows=3, cols=1, subplot_titles=("Elbow Method", "Silhouette Score", "Davies-Bouldin Index"))

# Add traces for each metric
fig.add_trace(
    go.Scatter(x=list(k_range), y=inertia_values, mode='lines+markers', name='Inertia'),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=list(k_range), y=silhouette_scores, mode='lines+markers', name='Silhouette Score'),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(x=list(k_range), y=davies_bouldin_scores, mode='lines+markers', name='Davies-Bouldin Index'),
    row=3, col=1
)

# Update layout
fig.update_layout(height=900, width=800, title_text="K-means Cluster Validation Metrics",
                  showlegend=False)

# Update y-axis titles
fig.update_yaxes(title_text="Inertia", row=1, col=1)
fig.update_yaxes(title_text="Silhouette Score (higher is better)", row=2, col=1)
fig.update_yaxes(title_text="Davies-Bouldin Index (lower is better)", row=3, col=1)

# Update x-axis titles
fig.update_xaxes(title_text="Number of Clusters (k)", row=3, col=1)

fig.show()

# 2. GAP STATISTIC METHOD
# Note: This can be computationally intensive

def calculate_gap_statistic(data, k_max=10, n_references=5, n_jobs=None):
    """
    Calculate the Gap statistic for determining the optimal number of clusters
    
    Parameters:
    -----------
    data : array-like
        The data to cluster
    k_max : int
        The maximum number of clusters to consider
    n_references : int
        Number of reference datasets to generate
    n_jobs : int or None
        Number of jobs to run in parallel
        
    Returns:
    --------
    gaps : array
        Gap statistics for each k
    s_k : array
        Standard deviations for each k
    """
    # Convert data to array if it's not already
    data = np.asarray(data)
    
    # Compute range of data for generating reference datasets
    data_min = data.min(axis=0)
    data_max = data.max(axis=0)
    
    # Initialize arrays to store gap statistics and standard errors
    gaps = np.zeros(k_max)
    s_k = np.zeros(k_max)
    
    # Compute gap statistic for each number of clusters
    for k in range(1, k_max + 1):
        # Compute clustering on real data
        kmeans = KMeans(n_clusters=k, random_state=42, n_init=10)
        kmeans.fit(data)
        log_w_k = np.log(kmeans.inertia_)
        
        # Initialize array to store reference log(W_k) values
        reference_log_w_k = np.zeros(n_references)
        
        # Generate reference datasets and cluster them
        for i in range(n_references):
            # Generate uniform random data in the same range as the original data
            reference = np.random.uniform(data_min, data_max, data.shape)
            
            # Cluster the reference data
            kmeans_ref = KMeans(n_clusters=k, random_state=i, n_init=10)
            kmeans_ref.fit(reference)
            reference_log_w_k[i] = np.log(kmeans_ref.inertia_)
        
        # Compute gap statistic
        gap = np.mean(reference_log_w_k) - log_w_k
        gaps[k-1] = gap
        
        # Compute standard deviation and error
        sdk = np.std(reference_log_w_k, ddof=1)
        s_k[k-1] = sdk * np.sqrt(1 + 1/n_references)
    
    return gaps, s_k

# Calculate gap statistic - this may take some time
print("Calculating Gap Statistic (this may take a few minutes)...")
gaps, s_k = calculate_gap_statistic(X, k_max=10, n_references=5)

# Find optimal k using the first maximum gap that satisfies the inequality gap[k] >= gap[k+1] - s[k+1]
optimal_k_gap = 1  # Default is 1 cluster
for k in range(len(gaps)-1):
    if gaps[k] >= gaps[k+1] - s_k[k+1]:
        optimal_k_gap = k + 1
        break

# Plot gap statistic
fig_gap = go.Figure()
fig_gap.add_trace(
    go.Scatter(x=list(range(1, len(gaps)+1)), y=gaps, mode='lines+markers', name='Gap Statistic')
)
fig_gap.add_trace(
    go.Scatter(x=[optimal_k_gap], y=[gaps[optimal_k_gap-1]], mode='markers', 
               marker=dict(size=12, symbol='star', color='red'),
               name=f'Optimal k={optimal_k_gap}')
)
fig_gap.update_layout(
    title='Gap Statistic Method',
    xaxis_title='Number of Clusters (k)',
    yaxis_title='Gap Statistic (higher is better)',
    width=800,
    height=500
)
fig_gap.show()

print(f"Optimal k according to Gap Statistic: {optimal_k_gap}")

# Determine optimal k from all methods
# Find k with highest silhouette score
optimal_k_silhouette = k_range[silhouette_scores.index(max(silhouette_scores))]

# Find k where the elbow occurs using the second derivative of inertia
def find_elbow_point(inertia):
    # Calculate second derivative
    d1_inertia = np.diff(inertia)
    d2_inertia = np.diff(d1_inertia)
    
    # Find the point of maximum second derivative (elbow point)
    elbow_index = np.argmax(np.abs(d2_inertia)) + 1  # +1 due to double differentiation
    return k_range[elbow_index]

optimal_k_elbow = find_elbow_point(inertia_values)

print(f"Optimal k according to Elbow Method: {optimal_k_elbow}")
print(f"Optimal k according to Silhouette Score: {optimal_k_silhouette}")
print(f"Optimal k according to Davies-Bouldin Index: {k_range[davies_bouldin_scores.index(min(davies_bouldin_scores))]}")

# Choose optimal k based on consensus from different methods
# For demonstration, we'll use the silhouette score method's result
optimal_k = optimal_k_silhouette
print(f"\nSelected optimal k = {optimal_k}")

# 3. RUN K-MEANS WITH OPTIMAL K
kmeans_optimal = KMeans(n_clusters=optimal_k, random_state=42, n_init=10)
cluster_labels = kmeans_optimal.fit_predict(X)

# Add cluster labels to the original dataframe
customer_features_clustered = customer_features.copy()
customer_features_clustered['cluster'] = cluster_labels

# 4. EVALUATE CLUSTER STABILITY WITH BOOTSTRAPPING
n_bootstraps = 100
bootstrap_results = np.zeros((n_bootstraps, len(X)))

for i in range(n_bootstraps):
    # Create a bootstrap sample
    bootstrap_indices = resample(np.arange(len(X)), replace=True, random_state=i)
    bootstrap_sample = X[bootstrap_indices]
    
    # Fit K-means to the bootstrap sample
    kmeans_bootstrap = KMeans(n_clusters=optimal_k, random_state=42, n_init=10)
    kmeans_bootstrap.fit(bootstrap_sample)
    
    # Predict cluster labels for all original data points
    bootstrap_labels = kmeans_bootstrap.predict(X)
    
    # Store the bootstrap results
    bootstrap_results[i] = bootstrap_labels

# Calculate Jaccard similarity matrix between all pairs of bootstrap samples
n_samples = len(X)
stability_matrix = np.zeros((n_samples, n_samples))
co_occurrence_matrix = np.zeros((n_samples, n_samples))

for i in range(n_samples):
    for j in range(i, n_samples):
        # Count how many times points i and j are clustered together
        same_cluster_count = sum(1 for b in range(n_bootstraps) 
                                if bootstrap_results[b, i] == bootstrap_results[b, j])
        co_occurrence_probability = same_cluster_count / n_bootstraps
        co_occurrence_matrix[i, j] = co_occurrence_matrix[j, i] = co_occurrence_probability

# Calculate cluster stability scores (average co-occurrence for points in the same cluster)
stability_scores = []
for k in range(optimal_k):
    cluster_indices = np.where(cluster_labels == k)[0]
    if len(cluster_indices) <= 1:
        stability_scores.append(1.0)  # Perfect stability for single-point clusters
        continue
        
    # Calculate average co-occurrence for all pairs in this cluster
    cluster_stability = 0
    pair_count = 0
    for i in range(len(cluster_indices)):
        for j in range(i+1, len(cluster_indices)):
            idx1, idx2 = cluster_indices[i], cluster_indices[j]
            cluster_stability += co_occurrence_matrix[idx1, idx2]
            pair_count += 1
    
    if pair_count > 0:
        cluster_stability /= pair_count
    else:
        cluster_stability = 1.0
        
    stability_scores.append(cluster_stability)

# Print stability scores
print("\nCluster Stability Analysis (Bootstrap):")
for k in range(optimal_k):
    print(f"Cluster {k}: Stability Score = {stability_scores[k]:.4f}, Size = {np.sum(cluster_labels == k)}")

# Calculate overall stability
overall_stability = np.mean(stability_scores)
print(f"Overall Cluster Stability: {overall_stability:.4f}")

# 5. VALIDATE CLUSTERS USING SILHOUETTE COEFFICIENT AND DAVIES-BOULDIN INDEX
silhouette_avg = silhouette_score(X, cluster_labels)
db_score = davies_bouldin_score(X, cluster_labels)

print("\nCluster Validation Metrics:")
print(f"Silhouette Score: {silhouette_avg:.4f} (higher is better, range [-1, 1])")
print(f"Davies-Bouldin Index: {db_score:.4f} (lower is better)")

# Calculate silhouette scores for each sample
silhouette_samples = np.zeros(len(X))
from sklearn.metrics import silhouette_samples
silhouette_values = silhouette_samples(X, cluster_labels)

# Create silhouette plot
plt.figure(figsize=(10, 6))
y_lower = 10

# Plot silhouette scores for each cluster
for i in range(optimal_k):
    cluster_silhouette_values = silhouette_values[cluster_labels == i]
    cluster_silhouette_values.sort()
    
    size_cluster_i = len(cluster_silhouette_values)
    y_upper = y_lower + size_cluster_i
    
    color = plt.cm.nipy_spectral(float(i) / optimal_k)
    plt.fill_betweenx(np.arange(y_lower, y_upper), 0, cluster_silhouette_values,
                     facecolor=color, edgecolor=color, alpha=0.7)
    
    # Label the silhouette plots with cluster numbers
    plt.text(-0.05, y_lower + 0.5 * size_cluster_i, str(i))
    
    # Compute the new y_lower for next plot
    y_lower = y_upper + 10

plt.title("Silhouette Plot for K-means Clustering")
plt.xlabel("Silhouette Coefficient Values")
plt.ylabel("Cluster Label")

# The vertical line for average silhouette score
plt.axvline(x=silhouette_avg, color="red", linestyle="--")
plt.yticks([])  # Clear the yaxis labels
plt.xticks([-0.1, 0, 0.2, 0.4, 0.6, 0.8, 1])
plt.xlim([-0.1, 1])
plt.savefig('silhouette_plot.png')
plt.close()

# Visualize clusters in 2D (using PCA if you have more than 2 features)
if 'PC1' in customer_features_clustered.columns and 'PC2' in customer_features_clustered.columns:
    # Use existing PCA components
    fig_clusters = px.scatter(
        customer_features_clustered, x='PC1', y='PC2',
        color='cluster', 
        title=f'K-means Clustering with k={optimal_k}',
        opacity=0.7,
        color_continuous_scale=px.colors.qualitative.G10
    )
else:
    # If you haven't done PCA yet, do a quick PCA for visualization
    from sklearn.decomposition import PCA
    pca_viz = PCA(n_components=2)
    X_pca_viz = pca_viz.fit_transform(X)
    
    # Create temporary dataframe for visualization
    viz_df = pd.DataFrame(X_pca_viz, columns=['PC1', 'PC2'])
    viz_df['cluster'] = cluster_labels
    
    fig_clusters = px.scatter(
        viz_df, x='PC1', y='PC2',
        color='cluster', 
        title=f'K-means Clustering with k={optimal_k}',
        opacity=0.7,
        color_continuous_scale=px.colors.qualitative.G10
    )

fig_clusters.update_layout(width=800, height=600)
fig_clusters.show()

# 6. ANALYZE CLUSTER CHARACTERISTICS
# Calculate mean values of features for each cluster
cluster_profiles = customer_features_clustered.groupby('cluster')[features_for_clustering].mean()
print("\nCluster Profiles (Mean Values):")
print(cluster_profiles)

# Create cluster profile radar chart
fig_radar = go.Figure()

# Add traces for each cluster
for cluster_id in range(optimal_k):
    # Get the profile for this cluster
    profile = cluster_profiles.iloc[cluster_id].values.tolist()
    
    # Add cluster profile to radar chart
    fig_radar.add_trace(go.Scatterpolar(
        r=profile,
        theta=features_for_clustering,
        fill='toself',
        name=f'Cluster {cluster_id}'
    ))

fig_radar.update_layout(
    polar=dict(
        radialaxis=dict(
            visible=True,
        )
    ),
    title="Cluster Profiles",
    width=800,
    height=600
)
fig_radar.show()

# Save the clustering results
customer_features_clustered.to_csv('customer_segments.csv', index=False)

print("\nClustering complete! Results saved to 'customer_segments.csv'")

k=2, Inertia=28965.30, Silhouette Score=0.5396, Davies-Bouldin=1.2436
k=3, Inertia=23178.55, Silhouette Score=0.5147, Davies-Bouldin=0.9676
k=4, Inertia=18539.92, Silhouette Score=0.4982, Davies-Bouldin=0.8765
k=5, Inertia=14391.45, Silhouette Score=0.4113, Davies-Bouldin=0.8425
k=6, Inertia=12485.39, Silhouette Score=0.4240, Davies-Bouldin=0.9211
k=7, Inertia=10868.84, Silhouette Score=0.4296, Davies-Bouldin=0.8586
k=8, Inertia=9443.50, Silhouette Score=0.4315, Davies-Bouldin=0.7925
k=9, Inertia=8425.26, Silhouette Score=0.3786, Davies-Bouldin=0.8260
k=10, Inertia=7645.78, Silhouette Score=0.3829, Davies-Bouldin=0.8104


Calculating Gap Statistic (this may take a few minutes)...


Optimal k according to Gap Statistic: 1
Optimal k according to Elbow Method: 5
Optimal k according to Silhouette Score: 2
Optimal k according to Davies-Bouldin Index: 8

Selected optimal k = 2

Cluster Stability Analysis (Bootstrap):
Cluster 0: Stability Score = 0.9915, Size = 6161
Cluster 1: Stability Score = 0.9677, Size = 1212
Overall Cluster Stability: 0.9796

Cluster Validation Metrics:
Silhouette Score: 0.5396 (higher is better, range [-1, 1])
Davies-Bouldin Index: 1.2436 (lower is better)



Cluster Profiles (Mean Values):
            recency  frequency    monetary  purchase_variability  tenure_days
cluster                                                                      
0        255.377211   1.735757   62.646621             11.232876    13.438403
1         94.361386  34.037954  188.473794            153.012435   248.251650



Clustering complete! Results saved to 'customer_segments.csv'


In [11]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np

# If you already have the customer_features_clustered DataFrame with cluster assignments:
# Count number of customers in each cluster
cluster_sizes = customer_features_clustered['cluster'].value_counts().sort_index()

# Display the results
print("Number of customers in each cluster:")
for cluster_id, size in cluster_sizes.items():
    print(f"Cluster {cluster_id}: {size} customers ({size/len(customer_features_clustered)*100:.2f}%)")

# Visualize the distribution
fig = px.bar(
    x=cluster_sizes.index,
    y=cluster_sizes.values,
    labels={'x': 'Cluster', 'y': 'Number of Customers'},
    title='Number of Customers per Cluster',
    text=cluster_sizes.values
)

fig.update_traces(texttemplate='%{text}', textposition='outside')
fig.update_layout(width=800, height=500)
fig.show()

# Create a pie chart to show the percentage distribution
fig_pie = px.pie(
    values=cluster_sizes.values,
    names=cluster_sizes.index,
    title='Customer Distribution Across Clusters (%)',
    labels={'label': 'Cluster', 'value': 'Percentage'}
)

fig_pie.update_traces(textinfo='percent+label')
fig_pie.update_layout(width=700, height=500)
fig_pie.show()

# Add cluster size information to the cluster profiles dataframe
cluster_profiles['cluster_size'] = cluster_sizes.values
cluster_profiles['percentage'] = (cluster_sizes.values / len(customer_features_clustered) * 100).round(2)

print("\nCluster profiles with size information:")
print(cluster_profiles)

Number of customers in each cluster:
Cluster 0: 6161 customers (83.56%)
Cluster 1: 1212 customers (16.44%)



Cluster profiles with size information:
            recency  frequency    monetary  purchase_variability  tenure_days  \
cluster                                                                         
0        255.377211   1.735757   62.646621             11.232876    13.438403   
1         94.361386  34.037954  188.473794            153.012435   248.251650   

         cluster_size  percentage  
cluster                            
0                6161       83.56  
1                1212       16.44  


In [12]:
cluster_profiles

recency  frequency    monetary  purchase_variability  tenure_days  \
cluster                                                                         
0        255.377211   1.735757   62.646621             11.232876    13.438403   
1         94.361386  34.037954  188.473794            153.012435   248.251650   

         cluster_size  percentage  
cluster                            
0                6161       83.56  
1                1212       16.44

In [15]:
customer_features_clustered

customer_id  recency  frequency    monetary  \
0     00235c62-e617-4eb0-a050-470c9f30e87f      441          1   26.990000   
1     00341635-2bff-4605-b3d0-ea405649659d        7          3   90.016667   
2     003fb56f-aa7f-4dd9-83bd-2209bb1076d4      224          1  129.520000   
3     004c365f-ed0a-4287-af51-77c29fc32803      128          2   30.275000   
4     004db925-5b13-4cf3-baac-df11e6e9b04b      203          2   59.600000   
...                                    ...      ...        ...         ...   
7368  ffebabfb-6506-429e-9a2f-7f8b3c7d0563      316          1  238.399600   
7369  ffed5f1a-267e-45f3-bdbd-f314b5c1d24a      305          1   17.921600   
7370  fff0fef1-ad54-4f33-8b38-5421f2458c07      488          2  433.040000   
7371  fff53181-88b9-442f-bf8b-efbffe3a71d4       27          1   39.940000   
7372  fff9b25c-663e-4680-8852-413b4132fad2      373          1   15.470000   

      purchase_variability first_purchase last_purchase  tenure_days  \
0                 0.000000     2023-11-08    2023-11-08            0   
1                 8.440292     2024-03-20    2025-01-15          301   
2                 0.000000     2024-06-12    2024-06-12            0   
3                12.296587     2024-07-30    2024-09-16           48   
4                37.349380     2024-06-17    2024-07-03           16   
...                    ...            ...           ...          ...   
7368              0.000000     2024-03-12    2024-03-12            0   
7369              0.000000     2024-03-23    2024-03-23            0   
7370             12.798633     2023-09-22    2023-09-22            0   
7371              0.000000     2024-12-26    2024-12-26            0   
7372              0.000000     2024-01-15    2024-01-15            0   

      purchases_per_day  spend_per_day  recency_ratio  customer_value_score  \
0              0.000000       0.000000       1.000000              0.003184   
1              0.009967       0.897176       0.023256              0.010575   
2              0.000000       0.000000       1.000000              0.014776   
3              0.041667       1.261458       2.666667              0.003688   
4              0.125000       7.450000      12.687500              0.007003   
...                 ...            ...            ...                   ...   
7368           0.000000       0.000000       1.000000              0.027085   
7369           0.000000       0.000000       1.000000              0.002159   
7370           0.000000       0.000000       1.000000              0.049223   
7371           0.000000       0.000000       1.000000              0.004648   
7372           0.000000       0.000000       1.000000              0.001882   

      cluster  
0           0  
1           1  
2           0  
3           0  
4           0  
...       ...  
7368        0  
7369        0  
7370        0  
7371        0  
7372        0  

[7373 rows x 13 columns]

In [14]:
data

order_id  purchase_amount currency  \
0      06c4bd28-eda3-42df-b819-aa19157a7d45            15.29      EUR   
1      3daaf5f9-b2c2-457a-9abf-330e279fc5c0            37.19      EUR   
2      33e1834f-db37-4a99-9be5-e45886b4dfd4            56.37      EUR   
3      0b51225c-0ffe-4b4a-990b-f266f58e51aa            24.19      EUR   
4      8d635007-5ab8-4680-988a-6ac5a93ea14b            24.79      USD   
...                                     ...              ...      ...   
51943  af9cd781-2114-45f4-969c-9f5bdacf0a24            19.98      EUR   
51944  18d722a3-8101-4e56-b70b-153c76294e19             9.99      EUR   
51945  b3b5ddda-50ce-4451-96da-eac3eef746a9            16.20      EUR   
51946  63fe50ef-72c5-4e2d-9bf9-aad49509f7fe             9.99      EUR   
51947  4a3d8cc9-f5f7-48d7-93d4-a26978a3d467            27.18      EUR   

      order_date                           customer_id  
0      1/22/2025  835ec885-114a-4f7f-b2a4-d7b45dc74411  
1      1/22/2025  74093a26-a976-42f8-b5c1-fcef1faebe9c  
2      1/22/2025  a27631c8-3fbd-4ace-a46f-c65b2c5928d2  
3      1/22/2025  2d5c1cad-07eb-439f-8ffa-9cd8ced6cea2  
4      1/22/2025  48a9bdca-dbf9-41b3-be54-93cf62d257da  
...          ...                                   ...  
51943   1/2/2023  ed1262ae-0fbb-4d9a-8797-d80400ca1d6b  
51944   1/2/2023  ed1262ae-0fbb-4d9a-8797-d80400ca1d6b  
51945   1/2/2023  e07d01e4-6a30-4c5a-9eef-4def9d4d90e2  
51946   1/1/2023  ed1262ae-0fbb-4d9a-8797-d80400ca1d6b  
51947   1/1/2023  98360512-fd49-48d5-8595-27c5f94d4c4b  

[51948 rows x 5 columns]

In [17]:
customer_features_clustered.to_csv('customer_features_clustered.csv', index=False)